# Generating standard normal random numbers

The task is to compare the generation of **many** standard normal random variables using `python`. We compare
- the **inversion method**;
- the **acceptence-rejection method**;
- the **Box-Muller method**;
- `numpy`'s default method.

**Remark** We use `numpy`'s standard RNG, without setting a seed or anything. I recommend reading [numpy.random](https://numpy.org/doc/stable/reference/random/index.html).


But first some libraries.

In [3]:
import numpy as np
from scipy.stats import norm ## provides normal quantile function and density
import timeit

## Numpy's standard method

Let us first use `numpy`s own function. In real life, we would stop right there and not even consider our alternatives...

Note that this is the **lazy** approach not recommended by `numpy`!

In [12]:
M = 100_000

In [13]:
%timeit np.random.normal(size=M)

1.8 ms ± 13.8 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)


For comparison, the **recommended** approach looks something like this:

In [14]:
seed = 12345
rng = np.random.Generator(np.random.PCG64(seed))
%timeit rng.normal(size=M)

1.08 ms ± 2.47 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)


In [15]:
seed = 12345
rng = np.random.Generator(np.random.MT19937(seed))
%timeit rng.normal(size=M)

1.31 ms ± 12.8 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)


I do not know why this is so much faster. Nonetheless, we stick with the lazy approach in this notebook.

## Inversion method

Now let us try the inversion method.

In [17]:
def normal_inversion_nonvec():
    """
    Simple, non-vectorized implementation of inversion method.

    """
    return norm.ppf(np.random.uniform())

In [18]:
def f1():
    x = np.zeros(M)
    for i in range(M):
        x[i] = normal_inversion_nonvec()
    return x

%timeit f1()

10 s ± 185 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


$10.5 s$ vs $2 ms$, i.e., $5000$ times slower! Let us try to be a bit more clever here!

In [19]:
def normal_inversion(M = 1):
    """
    Vectorized implementation of the inversion method.
    """
    return norm.ppf(np.random.uniform(size=M))

In [20]:
%timeit normal_inversion(M)

4.93 ms ± 21.2 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


What a relief! Now, we are in the same order of magnitude, roughly $3$ times slower.

Message: When using high level programming languages, **vectorization** is essential!

## Acceptence-rejection method

A simple, non-vectorized version might look as follows.

In [21]:
def acceptence_rejection_nonvec(f, g, g_gen, c):
    """Non-vectorized version of acceptence rejection method.
    
    Input:
        f ... target density. A scalar function.
        g ... auxiliary density. A scalar function.
        g_gen ... Function generating random numbers from the distribution g.
        c ... Constant s.t. f \le c * g
        
    Output:
        x ... A sample x from the distribution f.
    """
    accP = False
    while not accP:
        u = np.random.uniform()
        x = g_gen()
        accP = (u <= f(x) / (c * g(x)))
    return x

However, as we have already seen, this is no good. Let us, therefore, try to vectorize the function. This is now more tricky, as the number of iterations is random, as is the number of uniform random variables needed.

In [22]:
def acceptence_rejection(f, g, g_gen, c, M = 1):
    """Vectorized version of acceptence rejection method.
    
    Input:
        f ... target density. A vectorized function.
        g ... auxiliary density. A vectorized function.
        g_gen ... Function generating random numbers from the distribution g.
                  It is assumed to accept an argument "size" specifying the
                  size of the output.
        c ... Constant s.t. f \le c * g
        M ... number of samples to generate.
        
    Output:
        x ... A vector of samples x from the distribution f of length M.
    """
    x = np.empty(M)
    rejP = np.full(M, True) # initially, nothing is accepted
    Mremain = M # size of remaining random numbers
    while Mremain > 0:
        u = np.random.uniform(size=Mremain)
        x[rejP] = g_gen(size=Mremain)
        rejP[rejP] = (u > f(x[rejP]) / (c * g(x[rejP])))
        Mremain = np.sum(rejP)
    return x

Let us now specialize this abstract acceptence-rejection code for the case of the standard normal dustribution.

In [23]:
def laplace_pdf(x):
    """Density of the Laplace / double exponential distribution."""
    return 0.5 * np.exp(-np.abs(x))

const_normal_laplace = np.sqrt(2 * np.e / np.pi)

def f3():
    return acceptence_rejection(norm.pdf, laplace_pdf, np.random.laplace, 
                                const_normal_laplace, M)

%timeit f3()

12.2 ms ± 404 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


Still, the same order of magnitude, roughly $7$ times slower comparted to the numpy code.

## Box-Muller method

Finally, let us implement the Box-Muller method in `python`.

In [24]:
def box_muller(M = 1):
    """Generating normal random variables by Box-Muller."""
    # Use M+1 if M is odd.
    MEven = 2 * ((M + 1) // 2)
    u = np.random.uniform(size=MEven)
    u1, u2 = np.array_split(u, 2)
    theta = 2 * np.pi * u2
    rho = np.sqrt(-2*np.log(u1))
    x1 = rho * np.cos(theta)
    x2 = rho * np.sin(theta)
    return np.concatenate((x1,x2))[0:M]

In [25]:
%timeit box_muller(M)

2.59 ms ± 51.6 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


This is pretty fast, only $50\%$ slower than the numpy implementation - which might be achievable by aggressive optimization.

Summarizing:

Method | Time
:----- | ---:
`np.random.normal` | 1.8 ms
Using RNG explicitly | 1.1 ms
`normal_inversion_nonvec` | 10000 ms
`normal_inversion` | 4.9 ms
`acceptence_rejection` | 12.2 ms
`box_muller` | 2.6 ms

## Numpy's standard method

What method is numpy actually using? Let us look at the code at [github](https://github.com/numpy/numpy/blob/2afa142ae6ee121f6c75f28403526e35473ee6d5/numpy/random/mtrand/randomkit.c).

This is, in fact, the **polar method**.

# Monte Carlo

Now let us try two simple Monte Carlo simulation problems.

## First example

Let $X \sim \mathcal{N}(0,1)$ and compute $E[\sin(X)]$. We first use a non-vectorized, direct implementation.

In [26]:
def mc_nonvec(f, gen, M):
    """Monte Carlo simulation.
    
    Input:
        f ... scalar function
        gen ... function generating samples of X
        M ... number of samples
    Output:
        mu ... estimated expected value
        stat ... error estimate."""
    mu = 0.0
    mu2 = 0.0
    for _ in range(M):
        fx = f(gen())
        mu += fx
        mu2 += fx**2
    mu = mu / M
    mu2 = mu2 / M
    stat = 1.96 * np.sqrt((mu2 - mu**2) / M)
    return (mu, stat)

First compute the result and then time it.

In [27]:
M = 100_000
%timeit mc_nonvec(np.sin, np.random.normal, M)
(mu, stat) = mc_nonvec(np.sin, np.random.normal, M)
print("Result = {} +- {}".format(mu, stat))

244 ms ± 1.64 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
Result = -0.0040400178939893104 +- 0.004067415679941911


Now let us vectorize the code! Again, we assume a simple, scalar random variable.

In [28]:
def mc_scalar(f, gen, M):
    """Monte Carlo simulation.
    
    Input:
        f ... scalar function
        gen ... function generating samples of X
        M ... number of samples
    Output:
        mu ... estimated expected value
        stat ... error estimate."""
    fx = f(gen(size=M))
    mu = np.mean(fx)
    stat = 1.96 * np.std(fx) / np.sqrt(M)
    return (mu, stat)

In [29]:
M = 100_000
%timeit mc_scalar(np.sin, np.random.normal, M)
(mu, stat) = mc_scalar(np.sin, np.random.normal, M)
print("Result = {} +- {}".format(mu, stat))

3.07 ms ± 17 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)
Result = -0.00288397100551495 +- 0.004079097580249038


We see thar the vectorized version takes about $100$ times less.

What happens when we explicitly invoke the RNG?

In [30]:
M = 100_000
rng = np.random.Generator(np.random.MT19937(1234567))
%timeit mc_scalar(np.sin, rng.normal, M)
(mu, stat) = mc_scalar(np.sin, rng.normal, M)
print("Result = {} +- {}".format(mu, stat))

2.59 ms ± 27.8 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)
Result = 0.0009726901287408564 +- 0.004079955432807744


## Example 2

As a slightly more complicated example, suppose that we are given $N$ i.i.d. random variables $X_1, \ldots, X_N \sim \mathcal{N}(0,1)$. We want to compute
$$
E\left[ \max_{i=1, \ldots, N} X_i \right].
$$

We first try a completely naive, but also *straightforward* approach.

In [31]:
def mc_max_naive(M, N):
    mu = 0.0
    mu2 = 0.0
    for m in range(M):
        rmax = 0.0
        for n in range(N):
            x = np.random.normal()
            rmax = max(rmax, x)
        mu += rmax
        mu2 += rmax**2
    mu = mu / M
    mu2 = mu2 / M
    stat = 1.96 * np.sqrt((mu2 - mu**2) / M)
    return (mu, stat)

In [32]:
N = 100
M = 100000
%timeit mc_max_naive(M, N)
(mu, stat) = mc_max_naive(M, N)
print("Result = {} +- {}".format(mu, stat))

18.4 s ± 193 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
Result = 2.5060374275867434 +- 0.0026634519088117414


Now let us vectorize the inner loop.

In [33]:
def mc_max_partial_vec(M, N):
    mu = 0.0
    mu2 = 0.0
    for m in range(M):
        rmax = np.amax(np.random.normal(size = N))
        mu += rmax
        mu2 += rmax**2
    mu = mu / M
    mu2 = mu2 / M
    stat = 1.96 * np.sqrt((mu2 - mu**2) / M)
    return (mu, stat)

In [34]:
N = 100
M = 100000
%timeit mc_max_partial_vec(M, N)
(mu, stat) = mc_max_partial_vec(M, N)
print("Result = {} +- {}".format(mu, stat))

887 ms ± 12.2 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
Result = 2.5073359529089463 +- 0.0026680840247522725


This is roughly $20$ times faster.

Now we go for full vectorization.

In [35]:
def mc_max(M, N):
    x = np.random.normal(size=(M,N))
    rmax = np.amax(x, axis = 1)
    mu = np.mean(rmax)
    stat = 1.96 * np.std(rmax) / np.sqrt(M)
    return (mu, stat)

In [36]:
N = 100
M = 100000
%timeit mc_max(M, N)
(mu, stat) = mc_max(M, N)
print("Result = {} +- {}".format(mu, stat))

206 ms ± 4 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
Result = 2.5065048207481784 +- 0.0026666573615706035


This is $5$ times faster than the partially vectorized version and $100$ times faster than the naive version.

In [37]:
from sys import getsizeof
N = 100
M = 100000
x = np.random.normal(size=(M,N))
print("Size of x = {} MB".format(getsizeof(x)/1_000_000))

Size of x = 80.00012 MB


We see that the prize we pay is in memory. $80 MB$ is *nothing* today, but suppose that $N = 1000$, $M = 10^6$, then the memory would increase to roughly $8 GB$, which would probably cause some of your computers to crash.

Of course, we can take care of this with minimal performance cost, but at the price of quckly increasing complexity of the code.

Note that this dilemma between time and memory performance is an artefact of the programming language and has nothing todo with the problem itself!

# Conslusions

Comparing the `python` code with `C++`, we have the following (precomputed) timings (in ms each):

Function | Python | C++
-------- | ------:| ---:
`mc_nonvec` | 244 | 3
`mc_scalar` | 3 | 3
`mc_max_naive` | 18400 | 159
`mc_max_partial` | 887 | 159
`mc_max` | 206 | 181

Some remarks to keep in mind:
- `python` is ideal for prototyping and plaing around with concepts and algorithms.
- *Vectorization* is **essential** for scientific computing in `python`.
- `C++` is certainly more complicated to set up and it takes more work to get results for simple problems, even though this has improved a lot in the last 10 years.
- No *vectorization* is needed to get performing code in `C++`, the compiler takes care of it. Often this means that `C++`-code is **easier** to write than similarly performing `python` code, if even possible.
- Use best of both worlds: low level code called from high level language. E.g., `numpy` routines written in `C`.